In [ ]:
import io
import pandoc
import re
from xml.sax import make_parser
from xml.sax.saxutils import XMLFilterBase, XMLGenerator
import re
import bz2



class Project1Filter(XMLFilterBase):
    """This decides which SAX events to forward to the ContentHandler

    We will not forward events when we are inside any elements with a
    name specified in the 'tags_names_to_exclude' parameter
    """

    def __init__(self, tag_names_to_include, parent=None):
        super().__init__(parent)

        # set of tag names to exclude
        self._tag_names_to_include = tag_names_to_include

        # _valid_tag keeps track of opened project1 elements
        self._valid_tag = False
        self.current_tag = ''
        self.current_title = ''
        self.current_text = ''
        self.coord_found = False


    def startElement(self, name, attrs):
        if name in self._tag_names_to_include:
            self._valid_tag = True
            if name == 'title':
                self.current_tag = name
            elif name == 'text':
                self.current_tag = name
                

    def endElement(self, name):
        if name in self._tag_names_to_include:
            if self.current_tag == 'text' and self.coord_found:
                print(f"{self.current_title}")
#                 try:
#                     doc = pandoc.read(self.current_text, format='mediawiki')
#                 except Exception as e:
# #                     print(e)
#                     self._valid_tag = False
#                     self.current_tag = ''
#                     self.current_title = ''
#                     self.current_text = ''
#                     self.coord_found = False
#                     return None
                
                
                super().startElement('page', {})
                ###########
                super().startElement('title', {})
                super().characters(self.current_title)
                super().endElement('title')
                ############
                coords = re.search('{{Coord.*?}}', self.current_text).group()
                super().startElement('coords', {})
                super().characters(coords)
                super().endElement('coords')
                ############
#                 plain = pandoc.write(doc, format='plain')
#                 subset = " ".join(plain.split()[:])
#                 cleaned = re.sub('\W+',' ', subset).strip()
#                 cleaned = re.sub('ref',' ', cleaned).strip()
                super().startElement('text', {})
                super().characters(self.current_text)
                super().endElement('text') 
                super().characters('\n')
                ############
                super().endElement('page')
                
                self.current_tag = ''
                self.current_title = ''
                self.current_text = ''
                self._valid_tag = False
                self.coord_found = False
                
                
            if self.current_tag == 'text' and not self.coord_found:
                self.current_tag = ''
                self.current_title = ''
                self.current_text = ''
                self._valid_tag = False
                self.coord_found = False
                
            if self.current_tag == 'title': 
                self.current_tag = ''
                self._valid_tag = False


    def characters(self, content):
        if self._valid_tag:
            if self.current_tag == 'title':
                self.current_title += content
                
            elif self.current_tag == 'text':
                self.current_text += content
                if not self.coord_found:
                    if re.search('{{Coord.*?}}$', self.current_text):
#                         print("\tCoord found")
                        self.coord_found = True
                    



tag_names_to_include = {'title', 'text'}
reader = Project1Filter(tag_names_to_include, make_parser())

with open('wiki_coords.xml', 'w') as f:
    handler = XMLGenerator(f)
    reader.setContentHandler(handler)
    fp = bz2.open('Downloads/enwiki-latest-pages-articles-multistream.xml.bz2')
    reader.parse(fp)


Algeria
Alaska
American National Standards Institute
Apollo 11
Apollo 8
Aruba
Angola
Alberta
Afghanistan
Albania
Azerbaijan
Museum of Work
Alfred Nobel
Anatolia
Apple Inc.
Antigua and Barbuda
Aalborg Municipality
Aarhus
Geography of Azerbaijan
Anguilla
Ashmore and Cartier Islands
Park Güell
AOL
Akkadian Empire
Andaman Islands
Apollo 13
Archimedes
Arizona State University
American Airlines Flight 77
Adobe Inc.
Apollo 1
Apollo 10
Apollo 12
Apollo 14
Apollo 15
Apollo 17
Crandall University
Ann Arbor, Michigan
Acadia University
Annapolis Valley
Area 51
Advanced Micro Devices
Ajaigarh
Ajmer-Merwara
Azad Kashmir
Akihabara
Aung San Suu Kyi
Antarctic
Interior Alaska
Armageddon
Alexandria, Indiana
Alexandria, Louisiana
Azores
Outback
Arno
Belgium
Brazil
Black Sea
British Columbia
Bulgaria
Burgess Shale
The Bahamas
Bangladesh
Barbados
Bassas da India
Belarus
Belize
Bermuda
Bosnia and Herzegovina
Botswana
Brunei
British Virgin Islands
Burkina Faso
Geography of Brazil
Geography of the British Virg

In [8]:
fp = bz2.open('Downloads/enwiki-latest-pages-articles-multistream.xml.bz2')